<a href="https://colab.research.google.com/github/Foroogh-njf/Foroogh-njf/blob/main/big_data_graph_analytics.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Library**

## 1-import main python library

In [ ]:
import numpy as np
import pandas as pd
import os

### 1.1-main python lib - from lib section

In [ ]:
from scipy.io import mmread
from google.colab import files

## 2-import ploting library

In [ ]:
import matplotlib.pyplot as plt

## 3-instal Graph Lib/pakage

### snap

In [ ]:
!pip install snap-stanford

### python-igraph

In [ ]:
!pip install python-igraph # Voy a usar igraph para infomap (tiene un montón de algoritmos de comunidades incluido)
!apt-get install libcairo2-dev libjpeg-dev libgif-dev # Para graficar Igraph (acá dendrogramas)

### python-louvain

In [ ]:
!pip install python-louvain

### pycairo

In [ ]:
!pip install pycairo # Igraph usa Cairo para graficar

## 4-O2er Lib + instal

### Measure Execution Time

In [ ]:
!pip install ipython-autotime
 
%load_ext autotime

time: 137 µs (started: 2021-02-21 15:17:47 +00:00)


## 5-import graph Library

In [ ]:
import networkx as nx
import snap
import igraph as ig

time: 1.01 s (started: 2021-02-21 15:17:47 +00:00)


In [ ]:
from networkx.algorithms import community
from networkx.algorithms.community import greedy_modularity_communities

time: 1.88 ms (started: 2021-02-21 15:17:48 +00:00)


# My Function - Definition

In [ ]:
# A helper function we use later
def histogram(values):
    hist = {}
    for v in values:
        if v in hist.keys():
            hist[v] += 1
        else:
            hist[v] = 1
    return hist

time: 3.42 ms (started: 2021-02-21 15:17:48 +00:00)


In [ ]:
def extract_cluster_centerality(centerality_list,cluster_num,node_groupby_cluster):
  
  c_c = 0

  clusters_centerality = [0] * cluster_num

  for list_sub in node_groupby_cluster:
    
    sum_v = 0
  
    for n_idx in list_sub:
      sum_v = sum_v + centerality_list [n_idx]

    clusters_centerality[c_c] = sum_v
    c_c = c_c + 1
  return clusters_centerality

time: 6.27 ms (started: 2021-02-21 15:17:48 +00:00)


In [ ]:
# vertex_size_normalized = vertex_size_normalized_cal(coef,clusters_node_num_list)
def vertex_size_normalized_cal(coef,big_node_num,clusters_node_num_list):

  vertex_size_normalized = [(x * coef) / big_node_num for x in clusters_node_num_list ]

  return vertex_size_normalized


time: 2.68 ms (started: 2021-02-21 15:17:48 +00:00)


In [ ]:
# gamma = is_scale_free(min_deg,node_num,max_deg)
def is_scale_free(min_deg,node_num,max_deg):

  d = max_deg - min_deg
  gamma = np.log(node_num)/d
  return gamma

time: 3.61 ms (started: 2021-02-16 15:53:05 +00:00)


# load+read main data

## with open file

In [ ]:
with open('coAuthorsCiteseer.mtx','r') as f:
    lines = [line.rstrip() for line in f]

time: 172 ms (started: 2021-02-21 15:17:48 +00:00)


In [ ]:
lines

['%%MatrixMarket matrix coordinate pattern symmetric',
 '% kind: undirected graph',
 '227320 227320 814134',
 '2 1',
 '3 1',
 '4 1',
 '5 1',
 '6 1',
 '7 1',
 '8 1',
 '9 1',
 '10 1',
 '11 1',
 '12 1',
 '13 1',
 '14 1',
 '15 1',
 '16 1',
 '17 1',
 '18 1',
 '19 1',
 '20 1',
 '21 1',
 '22 1',
 '23 1',
 '18 2',
 '20 2',
 '5690 2',
 '11498 2',
 '23155 2',
 '29848 2',
 '34156 2',
 '55373 2',
 '76644 2',
 '76645 2',
 '105037 2',
 '120955 2',
 '130085 2',
 '132406 2',
 '148156 2',
 '154357 2',
 '197586 2',
 '197587 2',
 '219338 2',
 '219339 2',
 '16 3',
 '29757 3',
 '84925 3',
 '136272 3',
 '16 4',
 '26086 4',
 '95357 4',
 '97465 4',
 '97466 4',
 '97467 4',
 '97468 4',
 '124144 4',
 '124145 4',
 '124146 4',
 '124147 4',
 '124148 4',
 '124149 4',
 '133993 4',
 '153363 4',
 '153364 4',
 '155783 4',
 '167980 4',
 '167981 4',
 '167982 4',
 '7 5',
 '14 5',
 '19 5',
 '8 6',
 '10 6',
 '23 6',
 '14 7',
 '15 7',
 '19 7',
 '3112 7',
 '16567 7',
 '39553 7',
 '48781 7',
 '65442 7',
 '77773 7',
 '77774 7',


time: 14.2 ms (started: 2021-02-21 15:17:48 +00:00)


In [ ]:
data_file_GINFO  = lines[1]
data_file_G_INFO = lines[2]

time: 1.43 ms (started: 2021-02-21 15:17:48 +00:00)


In [ ]:
data_file_G_INFO

'227320 227320 814134'

time: 2.67 ms (started: 2021-02-21 15:17:48 +00:00)


In [ ]:
big_node_num = int(data_file_G_INFO[0:6])
print(big_node_num)

227320
time: 1.42 ms (started: 2021-02-21 15:17:48 +00:00)


In [ ]:
big_link_num = int(data_file_G_INFO[14:])
print(big_link_num)

814134
time: 1.53 ms (started: 2021-02-21 15:17:48 +00:00)


In [ ]:
len(lines)

814137

time: 3.24 ms (started: 2021-02-21 15:17:48 +00:00)


In [ ]:
big_link_num

814134

time: 3.13 ms (started: 2021-02-21 15:17:48 +00:00)


In [ ]:
big_S_node_holder_all = [0]*(big_link_num)
big_R_node_holder_all = [0]*(big_link_num)

for i in range(1,big_link_num+1):
  now_line = lines[i+2]
  #print(now_line)
  splited_line = now_line.split( )
  S_node_holder = int(splited_line[0])
  R_node_holder = int(splited_line[1])
  big_S_node_holder_all[i-1] = S_node_holder
  big_R_node_holder_all[i-1] = R_node_holder

time: 875 ms (started: 2021-02-21 15:17:48 +00:00)


In [ ]:
type(big_R_node_holder_all)

list

time: 2.93 ms (started: 2021-02-21 15:17:49 +00:00)


In [ ]:
len(big_R_node_holder_all)

814134

time: 2.74 ms (started: 2021-02-21 15:17:49 +00:00)


In [ ]:
len(big_S_node_holder_all)

814134

time: 2.58 ms (started: 2021-02-21 15:17:49 +00:00)


In [ ]:
print(big_S_node_holder_all)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
big_S_node_holder_all

[2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 18,
 20,
 5690,
 11498,
 23155,
 29848,
 34156,
 55373,
 76644,
 76645,
 105037,
 120955,
 130085,
 132406,
 148156,
 154357,
 197586,
 197587,
 219338,
 219339,
 16,
 29757,
 84925,
 136272,
 16,
 26086,
 95357,
 97465,
 97466,
 97467,
 97468,
 124144,
 124145,
 124146,
 124147,
 124148,
 124149,
 133993,
 153363,
 153364,
 155783,
 167980,
 167981,
 167982,
 7,
 14,
 19,
 8,
 10,
 23,
 14,
 15,
 19,
 3112,
 16567,
 39553,
 48781,
 65442,
 77773,
 77774,
 77775,
 77776,
 77777,
 102435,
 149863,
 154907,
 154908,
 161488,
 161489,
 161490,
 161491,
 161492,
 161493,
 161494,
 10,
 23,
 72562,
 11,
 13,
 22,
 23,
 13,
 14,
 22,
 145713,
 145714,
 155784,
 157949,
 157952,
 207272,
 207273,
 211310,
 211319,
 22,
 19,
 1753,
 16542,
 16554,
 16567,
 16568,
 26781,
 26782,
 29173,
 31668,
 39719,
 40667,
 40668,
 40669,
 40670,
 67289,
 83785,
 92216,
 94315,
 97787,
 97788,
 99694,
 10

time: 58.2 ms (started: 2021-02-21 15:17:49 +00:00)


# Create Graph

## Networkx : Make graph

### methode2

In [ ]:
# created an undirected graph with no vertices or edges 
big_nx = nx.Graph()

In [ ]:
big_node_num

In [ ]:
#big_nx.add_node(big_node_num)

for i in range (0,big_node_num):
  big_nx.add_node(i)


In [ ]:
big_nx.number_of_nodes()

In [ ]:
for i in range(0,len(big_S_node_holder_all)):
  big_S_n = big_S_node_holder_all[i]-1 # igraph node's id start at 0
  big_R_n = big_R_node_holder_all[i]-1
  # print(i)
  # print(big_S_n)
  # print(big_R_n)
  # print('--------')
  if big_S_n != big_R_n:
    big_nx.add_edge(big_S_n,big_R_n)

In [ ]:
big_nx.size()

In [ ]:
big_nx.number_of_nodes()

### Save networkx graph

In [ ]:
nx.write_gml(big_nx, "big_nx.gml.gz")
files.download('big_nx.gml.gz')

In [ ]:
nx.write_pajek(big_nx, "big_nx.net")
files.download('big_nx.net')

In [ ]:
nx.write_graphml_lxml(big_nx, "big_nx.graphml")  
files.download('big_nx.graphml')

In [ ]:
nx.write_edgelist(big_nx, "big_nx.edgelist")
files.download('big_nx.edgelist')

In [ ]:
nx.write_edgelist(big_nx, "big_nx2.edgelist.gz")
files.download('big_nx2.edgelist.gz')

###**read networkx graph**

In [ ]:
big_nx = nx.read_graphml("big_nx.graphml")  

time: 18 s (started: 2021-02-21 15:17:49 +00:00)


## SNAP : Make graph

In [ ]:
big_G1_snap = snap.TUNGraph.New()

time: 1.16 ms (started: 2021-02-21 15:18:07 +00:00)


In [ ]:
n=big_node_num 
for i in range(1,n+1):
  big_G1_snap.AddNode(i)
i

227320

time: 145 ms (started: 2021-02-21 15:18:07 +00:00)


In [ ]:
big_G1_snap.GetNodes()

227320

time: 2.71 ms (started: 2021-02-21 15:18:07 +00:00)


In [ ]:
for i in range(0,len(big_S_node_holder_all)):
  #print(i)
  big_S_n = big_S_node_holder_all[i]
  big_R_n = big_R_node_holder_all[i]
  #print(big_S_n)
  #print(big_R_n)
  #print('--------')
  if big_S_n != big_R_n:
    big_G1_snap.AddEdge(big_S_n,big_R_n)

time: 588 ms (started: 2021-02-21 15:18:07 +00:00)


In [ ]:
big_G1_snap.GetEdges()

814134

time: 3.36 ms (started: 2021-02-21 15:18:08 +00:00)


## IGRAPH - graph creation


### IGRAPH : Make graph

In [ ]:
# created an undirected graph with no vertices or edges 
big_igraph = ig.Graph()

In [ ]:
print(big_igraph)

In [ ]:
big_igraph.add_vertices(big_node_num)
print(big_node_num)

In [ ]:
print(big_igraph)

In [ ]:
# big_G1_igraph.add_edges([(1,0)])

In [ ]:
# type(big_S_n)

In [ ]:
len(big_S_node_holder_all)

In [ ]:
for i in range(0,len(big_S_node_holder_all)):
  big_S_n = big_S_node_holder_all[i]-1 # igraph node's id start at 0
  big_R_n = big_R_node_holder_all[i]-1
  print(i)
  # print(big_S_n)
  # print(big_R_n)
  # print('--------')
  if big_S_n != big_R_n:
    big_igraph.add_edges([(big_S_n,big_R_n)])

In [ ]:
# print(big_igraph)

###  save igraph

In [ ]:
big_igraph.write_gml('big_igraph_graph.glm')
files.download('big_igraph_graph.glm')

In [ ]:
big_igraph.write_gml('big_igraph_graph.gml')
files.download('big_igraph_graph.gml')

In [ ]:
big_igraph.write_graphml("big_igraph_graph.graphml")
files.download('big_igraph_graph.graphml')

In [ ]:
big_igraph.write_pickle("big_igraph_graph.pickle")
files.download('big_igraph_graph.pickle')

In [ ]:
big_igraph.write_pajek("big_igraph_graph.net")
files.download('big_igraph_graph.net')


In [ ]:
big_igraph.write_pajek("big_igraph_graph.pajek")
files.download('big_igraph_graph.pajek')

In [ ]:
big_igraph.write_edgelist("big_igraph_graph.edgelist")
files.download('big_igraph_graph.edgelist')

In [ ]:
big_igraph.write_lgl("big_igraph_graph.lgl")
files.download('big_igraph_graph.lgl')

In [ ]:
big_igraph.write_dot("big_igraph_graph.dot")
files.download('big_igraph_graph.dot')

In [ ]:
big_igraph.write_dot("big_igraph_graph.graphviz")
files.download('big_igraph_graph.graphviz')

In [ ]:
big_igraph.save("big_igraph_graph_2.graphml")
files.download('big_igraph_graph_2.graphml')

In [ ]:
big_igraph.save("big_igraph", format="gml")

###  load igraph

In [ ]:
# big_igraph  = ig.load('big_igraph_graph.gml')

In [ ]:
big_igraph  = ig.load("big_igraph_graph.graphml")

time: 1.41 s (started: 2021-02-21 15:19:06 +00:00)


In [ ]:
# big_igraph  = Graph.Read_GML('big_igraph_graph.gml')

In [ ]:
big_igraph  = ig.load('big_igraph_graph.net')

time: 1.08 s (started: 2021-02-13 16:29:25 +00:00)


# Attribte

## Node Degree

### IGRAPH - Degree

In [ ]:
big_igraph_deg_Count = big_igraph.degree()

time: 5.68 ms (started: 2021-02-21 15:19:21 +00:00)


In [ ]:
print(big_igraph_deg_Count)

[22, 21, 5, 21, 4, 4, 26, 5, 4, 4, 14, 1, 4, 61, 2, 10, 13, 45, 6, 20, 1, 4, 4, 1, 19, 2, 2, 12, 20, 20, 20, 20, 37, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 2, 2, 33, 3, 14, 9, 4, 4, 7, 4, 22, 6, 2, 3, 2, 3, 3, 3, 8, 1, 5, 3, 6, 8, 25, 2, 35, 5, 4, 39, 6, 5, 6, 7, 10, 7, 7, 7, 7, 13, 56, 10, 7, 66, 8, 5, 19, 8, 4, 20, 7, 16, 20, 6, 11, 6, 11, 7, 9, 5, 10, 8, 6, 16, 11, 23, 9, 3, 8, 8, 23, 14, 6, 2, 35, 8, 7, 4, 4, 139, 4, 20, 4, 70, 6, 7, 16, 20, 13, 7, 4, 3, 3, 3, 18, 2, 6, 6, 3, 2, 3, 4, 2, 107, 2, 2, 4, 2, 3, 3, 3, 79, 3, 17, 13, 46, 2, 2, 3, 5, 11, 5, 15, 14, 5, 6, 8, 6, 6, 7, 6, 11, 6, 33, 6, 22, 9, 6, 16, 3, 2, 4, 2, 3, 3, 6, 4, 1, 3, 3, 50, 9, 9, 9, 47, 19, 7, 33, 2, 42, 28, 32, 2, 6, 29, 27, 60, 23, 27, 35, 5, 7, 5, 5, 9, 6, 14, 3, 3, 6, 17, 3, 1, 2, 3, 8, 12, 5, 2, 2, 9, 2, 2, 27, 1, 15, 1, 17, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 30, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 11, 43, 23, 27, 19, 24, 11, 80, 11, 99, 11, 11, 5, 5, 4, 5, 3, 5,

In [ ]:
big_igraph_deg_Count_df = pd.DataFrame(big_igraph_deg_Count)
big_igraph_deg_Count_df.to_csv('big_igraph_deg_Count.csv',index=False)
files.download('big_igraph_deg_Count.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 365 ms (started: 2021-02-21 15:19:23 +00:00)


In [ ]:
type(big_igraph_deg_Count.index(1))

int

time: 3.29 ms (started: 2021-02-21 15:19:23 +00:00)


## K-Core

### SNAP - K-Core

A graph method that returns the number of nodes in 
each core of order K (where K=0, 1, …).

In [ ]:
big_snap_kValue, big_snap_CoreIDSzV = big_G1_snap.GetKCoreNodes()

time: 274 ms (started: 2021-02-21 15:19:25 +00:00)


In [ ]:
big_snap_kcore_nodenum_list = [0]* len(big_snap_CoreIDSzV)
cc = 0

for item in big_snap_CoreIDSzV:
  cc = cc+1
  big_snap_kcore_nodenum_list[cc-1] = (item.GetVal1(),item.GetVal2())

time: 3.62 ms (started: 2021-02-21 15:19:25 +00:00)


In [ ]:
big_df_snap_kcore_nodenum = pd.DataFrame(big_snap_kcore_nodenum_list)
big_df_snap_kcore_nodenum.to_csv('big_snap_kcore_nodenum.csv',index=False)
files.download('big_snap_kcore_nodenum.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 10.1 ms (started: 2021-02-21 15:19:25 +00:00)


A graph method that returns the number of edges in each core 
of order K (where K=0, 1, …).

In [ ]:
big_snap_kValue, big_snap_CoreIDSzV = big_G1_snap.GetKCoreEdges()

time: 264 ms (started: 2021-02-21 15:19:25 +00:00)


In [ ]:
for item in big_snap_CoreIDSzV:
  filename = 'core' + str(item.GetVal1()) + '.txt'
  Core = big_G1_snap.GetKCore(item.GetVal1())
  Core.SaveEdgeList(filename)
  files.download(filename)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 15.7 s (started: 2021-02-21 15:19:25 +00:00)


### Networkx - K-Core

In [ ]:
big_nx_each_node_core_number = nx.core_number(big_nx)

time: 3.18 s (started: 2021-02-21 15:19:41 +00:00)


In [ ]:
print(big_nx_each_node_core_number)


{'0': 5, '1': 8, '2': 4, '3': 6, '4': 4, '5': 4, '6': 5, '7': 4, '8': 4, '9': 4, '10': 4, '11': 1, '12': 4, '13': 7, '14': 2, '15': 4, '16': 7, '17': 7, '18': 4, '19': 5, '20': 1, '21': 4, '22': 4, '23': 1, '24': 11, '25': 2, '26': 2, '27': 4, '28': 20, '29': 20, '30': 20, '31': 20, '32': 20, '33': 20, '34': 20, '35': 20, '36': 20, '37': 20, '38': 20, '39': 20, '40': 20, '41': 20, '42': 20, '43': 20, '44': 20, '45': 20, '46': 20, '47': 20, '48': 20, '49': 2, '50': 2, '51': 6, '52': 3, '53': 6, '54': 3, '55': 3, '56': 4, '57': 4, '58': 4, '59': 5, '60': 4, '61': 2, '62': 2, '63': 2, '64': 3, '65': 3, '66': 3, '67': 5, '68': 1, '69': 4, '70': 3, '71': 3, '72': 3, '73': 8, '74': 2, '75': 10, '76': 3, '77': 4, '78': 9, '79': 4, '80': 4, '81': 4, '82': 7, '83': 7, '84': 7, '85': 7, '86': 7, '87': 7, '88': 7, '89': 7, '90': 7, '91': 7, '92': 15, '93': 7, '94': 4, '95': 8, '96': 7, '97': 4, '98': 15, '99': 7, '100': 7, '101': 8, '102': 5, '103': 8, '104': 5, '105': 5, '106': 4, '107': 8, '108

**Returns the k-core of G.**

A k-core is a maximal subgraph that contains nodes of degree k or more.

In [ ]:
big_nx_k_core = nx.k_core(big_nx)

time: 3.5 s (started: 2021-02-21 15:19:44 +00:00)


In [ ]:
nx.write_edgelist(big_nx_k_core, "test.edgelist.txt", data=False)

time: 10.1 ms (started: 2021-02-21 15:19:48 +00:00)


In [ ]:
print(big_nx_k_core)


time: 1.36 ms (started: 2021-02-21 15:19:48 +00:00)


## Node Centrality

### Centerality - K-Shell 

#### Igraph - Centerality - K-Shell

Finds the coreness (shell index) of the vertices of the network.

In [ ]:
big_igraph_centerality_KShell = big_igraph.coreness()

time: 122 ms (started: 2021-02-21 15:19:48 +00:00)


In [ ]:
big_igraph_centerality_KShell

[5,
 8,
 4,
 6,
 4,
 4,
 5,
 4,
 4,
 4,
 4,
 1,
 4,
 7,
 2,
 4,
 7,
 7,
 4,
 5,
 1,
 4,
 4,
 1,
 11,
 2,
 2,
 4,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 20,
 2,
 2,
 6,
 3,
 6,
 3,
 3,
 4,
 4,
 4,
 5,
 4,
 2,
 2,
 2,
 3,
 3,
 3,
 5,
 1,
 4,
 3,
 3,
 3,
 8,
 2,
 10,
 3,
 4,
 9,
 4,
 4,
 4,
 7,
 7,
 7,
 7,
 7,
 7,
 7,
 7,
 7,
 7,
 15,
 7,
 4,
 8,
 7,
 4,
 15,
 7,
 7,
 8,
 5,
 8,
 5,
 5,
 4,
 8,
 4,
 8,
 8,
 5,
 9,
 6,
 8,
 4,
 3,
 8,
 6,
 8,
 8,
 4,
 2,
 6,
 3,
 4,
 4,
 4,
 15,
 4,
 16,
 4,
 9,
 4,
 4,
 8,
 7,
 6,
 4,
 4,
 3,
 3,
 3,
 6,
 2,
 3,
 4,
 2,
 2,
 2,
 2,
 2,
 58,
 2,
 2,
 2,
 2,
 3,
 3,
 3,
 28,
 3,
 5,
 5,
 9,
 2,
 2,
 2,
 5,
 7,
 5,
 10,
 7,
 5,
 6,
 6,
 6,
 6,
 6,
 6,
 6,
 6,
 6,
 6,
 6,
 6,
 6,
 6,
 2,
 2,
 2,
 2,
 3,
 3,
 3,
 3,
 1,
 1,
 3,
 12,
 4,
 4,
 6,
 6,
 7,
 4,
 13,
 2,
 22,
 6,
 22,
 2,
 6,
 20,
 20,
 33,
 20,
 20,
 20,
 5,
 5,
 5,
 5,
 5,
 3,
 3,
 3,
 3,
 3,
 4,
 3,
 1,
 1,
 3,
 4,
 8,
 3,
 2,
 2,
 4,


time: 13.3 ms (started: 2021-02-21 15:19:48 +00:00)


In [ ]:
print(big_igraph_centerality_KShell)

[5, 8, 4, 6, 4, 4, 5, 4, 4, 4, 4, 1, 4, 7, 2, 4, 7, 7, 4, 5, 1, 4, 4, 1, 11, 2, 2, 4, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 20, 2, 2, 6, 3, 6, 3, 3, 4, 4, 4, 5, 4, 2, 2, 2, 3, 3, 3, 5, 1, 4, 3, 3, 3, 8, 2, 10, 3, 4, 9, 4, 4, 4, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 15, 7, 4, 8, 7, 4, 15, 7, 7, 8, 5, 8, 5, 5, 4, 8, 4, 8, 8, 5, 9, 6, 8, 4, 3, 8, 6, 8, 8, 4, 2, 6, 3, 4, 4, 4, 15, 4, 16, 4, 9, 4, 4, 8, 7, 6, 4, 4, 3, 3, 3, 6, 2, 3, 4, 2, 2, 2, 2, 2, 58, 2, 2, 2, 2, 3, 3, 3, 28, 3, 5, 5, 9, 2, 2, 2, 5, 7, 5, 10, 7, 5, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 2, 2, 2, 2, 3, 3, 3, 3, 1, 1, 3, 12, 4, 4, 6, 6, 7, 4, 13, 2, 22, 6, 22, 2, 6, 20, 20, 33, 20, 20, 20, 5, 5, 5, 5, 5, 3, 3, 3, 3, 3, 4, 3, 1, 1, 3, 4, 8, 3, 2, 2, 4, 2, 2, 5, 1, 4, 1, 5, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 23, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 4, 4, 4, 4, 3, 4, 4, 4, 4, 5, 4, 5, 5, 2, 2, 4, 5, 3, 1, 4, 43, 5, 2, 4, 4

In [ ]:
sorted( [(x,i) for (i,x) in enumerate(big_igraph_centerality_KShell)], reverse=True )[:10] 

[(86, 17330),
 (86, 17329),
 (86, 17328),
 (86, 17326),
 (86, 17325),
 (86, 17324),
 (86, 17323),
 (86, 17322),
 (86, 17321),
 (86, 17320)]

time: 191 ms (started: 2021-02-21 15:19:48 +00:00)


In [ ]:
big_igraph_centerality_KShell_top10 = sorted( [(x,i) for (i,x) in enumerate(big_igraph_centerality_KShell)], reverse=True )[:10] 

time: 151 ms (started: 2021-02-21 15:19:48 +00:00)


In [ ]:
big_igraph_KShell_df = pd.DataFrame(big_igraph_centerality_KShell)
big_igraph_KShell_df.to_csv('big_igraph_centerality_KShell.csv',index=False)
files.download('big_igraph_centerality_KShell.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 251 ms (started: 2021-02-21 15:19:48 +00:00)


### Centerality - HIT

#### igraph - Centerality - HIT

**Authority Score**

In [ ]:
big_igraph_auth_score = big_igraph.authority_score()

time: 1.19 s (started: 2021-02-21 15:19:48 +00:00)


In [ ]:
print(big_igraph_auth_score)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
sorted( [(x,i) for (i,x) in enumerate(big_igraph_auth_score)], reverse=True )[:10] 

[(1.0, 17262),
 (0.996536916057218, 17313),
 (0.9928842234343684, 15273),
 (0.9903870256291882, 8539),
 (0.9892111478606731, 17290),
 (0.9867326120567205, 4570),
 (0.9854238466123338, 17330),
 (0.9854238466123338, 17326),
 (0.9854238466123338, 17320),
 (0.9854238466123338, 17299)]

time: 362 ms (started: 2021-02-21 15:19:50 +00:00)


In [ ]:
big_igraph_auth_score_top10 = sorted( [(x,i) for (i,x) in enumerate(big_igraph_auth_score)], reverse=True )[:10] 

time: 308 ms (started: 2021-02-21 15:19:50 +00:00)


In [ ]:
big_igraph_auth_score_sorted = sorted( [(x,i) for (i,x) in enumerate(big_igraph_auth_score)], reverse=True )[:]

time: 291 ms (started: 2021-02-21 15:19:51 +00:00)


In [ ]:
big_igraph_auth_df = pd.DataFrame(big_igraph_auth_score)
big_igraph_auth_df.to_csv('big_igraph_auth_score.csv',index=False)
files.download('big_igraph_auth_score.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 633 ms (started: 2021-02-21 15:19:51 +00:00)


**HUB Score**

In [ ]:
big_igraph_hub_score = big_igraph.hub_score()

time: 1.24 s (started: 2021-02-21 15:19:52 +00:00)


In [ ]:
print(big_igraph_hub_score)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
sorted( [(x,i) for (i,x) in enumerate(big_igraph_hub_score)], reverse=True )[:10] 

[(1.0, 17262),
 (0.996536916057218, 17313),
 (0.9928842234343684, 15273),
 (0.9903870256291882, 8539),
 (0.9892111478606731, 17290),
 (0.9867326120567205, 4570),
 (0.9854238466123338, 17330),
 (0.9854238466123338, 17326),
 (0.9854238466123338, 17320),
 (0.9854238466123338, 17299)]

time: 361 ms (started: 2021-02-21 15:19:53 +00:00)


In [ ]:
big_igraph_hub_score_top10 = sorted( [(x,i) for (i,x) in enumerate(big_igraph_hub_score)], reverse=True )[:10] 

time: 309 ms (started: 2021-02-21 15:19:53 +00:00)


In [ ]:
big_igraph_hub_df = pd.DataFrame(big_igraph_hub_score)
big_igraph_hub_df.to_csv('big_igraph_hub_score.csv',index=False)
files.download('big_igraph_hub_score.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 574 ms (started: 2021-02-21 15:19:54 +00:00)


### Centerality - Page Rank

#### Igraph - Centerality - Page Rank

In [ ]:
big_igraph_PRankH = big_igraph.pagerank()

time: 549 ms (started: 2021-02-21 15:19:54 +00:00)


In [ ]:
len(big_igraph_PRankH)

227320

time: 2.65 ms (started: 2021-02-21 15:19:55 +00:00)


In [ ]:
print(big_igraph_PRankH)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
sorted( [(x,i) for (i,x) in enumerate(big_igraph_PRankH)], reverse=True )[:10] 

[(0.0009541554345746803, 1155),
 (0.0002337991727159533, 408),
 (0.00023313659387182343, 431),
 (0.0001797625577251831, 3872),
 (0.00017976255772517724, 3877),
 (0.000179762557725173, 3878),
 (0.00017927321594336343, 3874),
 (0.0001422955545751227, 8893),
 (0.00014131990032478604, 3084),
 (0.0001381292147010133, 3083)]

time: 356 ms (started: 2021-02-21 15:19:55 +00:00)


In [ ]:
big_igraph_PRankH_top10 = sorted( [(x,i) for (i,x) in enumerate(big_igraph_PRankH)], reverse=True )[:10] 

time: 305 ms (started: 2021-02-21 15:19:56 +00:00)


In [ ]:
big_igraph_PRankH_df = pd.DataFrame(big_igraph_PRankH)
big_igraph_PRankH_df.to_csv('big_igraph_PRankH.csv',index=False)
files.download('big_igraph_PRankH.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 589 ms (started: 2021-02-21 15:19:56 +00:00)


# **Community Detection**

## **1- Newman**

### SNAP - Newman

In [ ]:
big_modularity, big_CmtyV = big_G1_snap.CommunityGirvanNewman()

In [ ]:

for Cmty in big_CmtyV:
    print("Community: ")
    for NI in Cmty:
        print(NI)
print("The modularity of the network is %f" % big_modularity)

### Networkx - Newman

In [ ]:
big_nx_girvan_newman_communities_generator = community.girvan_newman(big_nx)

In [ ]:
top_level_communities = next(big_nx_girvan_newman_communities_generator)
next_level_communities = next(big_nx_girvan_newman_communities_generator)
sorted(map(sorted, next_level_communities))

In [ ]:
# girvan_newman(big_nx, most_valuable_edge=None)

## **2-louvain**

### **igraph - louvain**

In [ ]:
# best level result only - result clusters with highest modularity value

time: 786 µs (started: 2021-02-21 15:19:57 +00:00)


In [ ]:
big_igraph_louvain_best_modularity =  big_igraph.community_multilevel(weights=None, return_levels=False)

time: 2.82 s (started: 2021-02-21 15:19:57 +00:00)


#### **igraph - louvain - Exract cluster properties**

In [ ]:
my_cl_lou = big_igraph_louvain_best_modularity

time: 995 µs (started: 2021-02-21 15:19:59 +00:00)


In [ ]:
type (big_igraph_louvain_best_modularity)

igraph.clustering.VertexClustering

time: 2.6 ms (started: 2021-02-21 15:19:59 +00:00)


In [ ]:
big_igraph_louvain_best_modularity_cluster_num = len(big_igraph_louvain_best_modularity)
print ('The final number of clusters = ',big_igraph_louvain_best_modularity_cluster_num)


The final number of clusters =  248
time: 2.37 ms (started: 2021-02-21 15:19:59 +00:00)


In [ ]:
my_louvine_cl_membership_list = my_cl_lou.membership

time: 1.93 ms (started: 2021-02-21 15:19:59 +00:00)


group nodes by their cluster number  
cluster number was obtaine via my_cl_membership_list varaible  
in the result varaible, we have N sub_list  
each sub_list have Pj member  
j is Sublist ittrator  
and pj is the tottal number of node's that share that cluster  
  
for example sublist # 0, have all node idx which belongs to cluster # 0


In [ ]:
louvine_memb_d = my_louvine_cl_membership_list
ig_comm_louvine_node_group_by_cluster_number = pd.Series(range(len(louvine_memb_d))).groupby(louvine_memb_d, sort=False).apply(list).tolist()

time: 227 ms (started: 2021-02-21 15:19:59 +00:00)


##### **extract each cluster's subgraph and edge list - louvine community**

extract subgraph and each list of each cluster - here we didnt make super node based graph yet

In [ ]:
cc = 0

for louvine_cluster in my_cl_lou:

  c_l =len(louvine_cluster)
   
  this_g_name      = 'sb_g_' + str(cc) + '.graphml'
  this_g_edge_name = 'sb_g_' + str(cc) + '_edge.npy'

  np.save(this_g_edge_name, louvine_cluster)

  # files.download(this_g_edge_name)

  cl_g_sb = my_cl_lou.subgraph(cc)
  
  cl_g_sb.write_graphml(this_g_name)

  # files.download(this_g_name)

  cc=cc+1

time: 4.24 s (started: 2021-02-21 15:20:00 +00:00)


##### **extract each cluster's total cenetrality value**

extract total centrality of each cluster  
cluster centerality = sum of each node's centrality in that cluster  

In [ ]:
# clusters_centerality  = extract_cluster_centerality(centerality_list,cluster_num,node_groupby_cluster):

time: 860 µs (started: 2021-02-21 15:20:04 +00:00)


In [ ]:
louvain_cluster_num = big_igraph_louvain_best_modularity_cluster_num

time: 987 µs (started: 2021-02-21 15:20:04 +00:00)


In [ ]:
this_ig_com_n_gb_cl_num = ig_comm_louvine_node_group_by_cluster_number

time: 921 µs (started: 2021-02-21 15:20:04 +00:00)


###### HIT Centerality

In [ ]:
clusters_louvain_ig_auth_centerality = extract_cluster_centerality(big_igraph_auth_score,louvain_cluster_num,this_ig_com_n_gb_cl_num)

time: 36.3 ms (started: 2021-02-21 15:20:04 +00:00)


In [ ]:
np.save("clusters_louvain_ig_auth_centerality.npy", clusters_louvain_ig_auth_centerality)
files.download('clusters_louvain_ig_auth_centerality.npy')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 6.64 ms (started: 2021-02-21 15:20:04 +00:00)


In [ ]:
big_ig_lou_cl_auth_cen_df = pd.DataFrame(clusters_louvain_ig_auth_centerality)
big_ig_lou_cl_auth_cen_df.to_csv('clusters_louvain_ig_auth_centerality.csv',index=False)
files.download('clusters_louvain_ig_auth_centerality.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 10.4 ms (started: 2021-02-21 15:20:04 +00:00)


In [ ]:
clusters_louvain_ig_hub_centerality = extract_cluster_centerality(big_igraph_hub_score,louvain_cluster_num,this_ig_com_n_gb_cl_num)

time: 34.1 ms (started: 2021-02-21 15:20:04 +00:00)


In [ ]:
np.save("clusters_louvain_ig_hub_centerality.npy", clusters_louvain_ig_hub_centerality)
files.download('clusters_louvain_ig_hub_centerality.npy')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 6.77 ms (started: 2021-02-21 15:20:04 +00:00)


In [ ]:
big_ig_lou_cl_hub_cen_df = pd.DataFrame(clusters_louvain_ig_hub_centerality)
big_ig_lou_cl_hub_cen_df.to_csv('clusters_louvain_ig_hub_centerality.csv',index=False)
files.download('clusters_louvain_ig_hub_centerality.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 12.3 ms (started: 2021-02-21 15:20:04 +00:00)


###### Page Rank Centerality

In [ ]:
clusters_louvain_ig_PRank_centerality = extract_cluster_centerality(big_igraph_PRankH,louvain_cluster_num,this_ig_com_n_gb_cl_num)

time: 28.9 ms (started: 2021-02-21 15:20:04 +00:00)


In [ ]:
np.save("clusters_louvain_ig_PRank_centerality.npy", clusters_louvain_ig_PRank_centerality)
files.download('clusters_louvain_ig_PRank_centerality.npy')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 6.53 ms (started: 2021-02-21 15:20:04 +00:00)


In [ ]:
big_ig_lou_cl_PR_cen_df = pd.DataFrame(clusters_louvain_ig_PRank_centerality)
big_ig_lou_cl_PR_cen_df.to_csv('clusters_louvain_ig_PRank_centerality.csv',index=False)
files.download('clusters_louvain_ig_PRank_centerality.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 11.7 ms (started: 2021-02-21 15:20:04 +00:00)


###### KShell Centerality

In [ ]:
clusters_louvain_ig_KShell_centerality = extract_cluster_centerality(big_igraph_centerality_KShell,louvain_cluster_num,this_ig_com_n_gb_cl_num)

time: 29.5 ms (started: 2021-02-21 15:20:04 +00:00)


In [ ]:
np.save("clusters_louvain_ig_KShell_centerality.npy", clusters_louvain_ig_KShell_centerality)
files.download('clusters_louvain_ig_KShell_centerality.npy')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 7.25 ms (started: 2021-02-21 15:20:04 +00:00)


In [ ]:
big_ig_lou_cl_kshell_cen_df = pd.DataFrame(clusters_louvain_ig_KShell_centerality)
big_ig_lou_cl_kshell_cen_df.to_csv('clusters_louvain_ig_KShell_centerality.csv',index=False)
files.download('clusters_louvain_ig_KShell_centerality.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 16.2 ms (started: 2021-02-21 15:20:04 +00:00)


#### **igraph - louvain === Extract each cluster's totall node number**

In [ ]:
cc = 0

# total_clusters_num = len(my_cl_lou)

louvain_clusters_node_num = [0] * louvain_cluster_num

for louvain_cluster in my_cl_lou:

  c_l =len(louvain_cluster)

  print ('cluster # ', cc , 'size(node num) = ' , c_l)

  louvain_clusters_node_num[cc] = c_l

  cc=cc+1

cluster #  0 size(node num) =  1164
cluster #  1 size(node num) =  686
cluster #  2 size(node num) =  1469
cluster #  3 size(node num) =  5380
cluster #  4 size(node num) =  1446
cluster #  5 size(node num) =  4370
cluster #  6 size(node num) =  1120
cluster #  7 size(node num) =  479
cluster #  8 size(node num) =  5823
cluster #  9 size(node num) =  1347
cluster #  10 size(node num) =  3412
cluster #  11 size(node num) =  11174
cluster #  12 size(node num) =  1531
cluster #  13 size(node num) =  2223
cluster #  14 size(node num) =  1177
cluster #  15 size(node num) =  3604
cluster #  16 size(node num) =  950
cluster #  17 size(node num) =  702
cluster #  18 size(node num) =  1184
cluster #  19 size(node num) =  964
cluster #  20 size(node num) =  1513
cluster #  21 size(node num) =  557
cluster #  22 size(node num) =  689
cluster #  23 size(node num) =  6468
cluster #  24 size(node num) =  833
cluster #  25 size(node num) =  5208
cluster #  26 size(node num) =  992
cluster #  27 size(

In [ ]:
len (louvain_clusters_node_num)

248

time: 2.87 ms (started: 2021-02-21 16:30:17 +00:00)


In [ ]:
# print (clusters_node_num)

time: 639 µs (started: 2021-02-21 16:30:18 +00:00)


In [ ]:
big_igraph_louvain_clusters_node_num = louvain_clusters_node_num

time: 1.38 ms (started: 2021-02-21 16:30:19 +00:00)


In [ ]:
print (big_igraph_louvain_clusters_node_num)

[1164, 686, 1469, 5380, 1446, 4370, 1120, 479, 5823, 1347, 3412, 11174, 1531, 2223, 1177, 3604, 950, 702, 1184, 964, 1513, 557, 689, 6468, 833, 5208, 992, 1368, 643, 418, 2215, 1605, 258, 2365, 438, 864, 1566, 1961, 1878, 1994, 259, 1561, 681, 2516, 1850, 3224, 403, 719, 1484, 529, 6040, 3975, 673, 1113, 867, 244, 315, 836, 2893, 1327, 284, 1395, 1459, 2128, 4068, 534, 2010, 2308, 1105, 1131, 374, 377, 1473, 660, 762, 676, 1243, 982, 1543, 943, 580, 1069, 1636, 879, 763, 775, 16, 1926, 843, 947, 1119, 2009, 9, 901, 853, 571, 989, 1202, 922, 1535, 642, 727, 1491, 617, 2369, 1121, 2264, 705, 677, 459, 1403, 572, 343, 593, 882, 778, 25, 1139, 1138, 1597, 1028, 1646, 365, 434, 1762, 1209, 37, 2558, 19, 598, 1666, 901, 743, 324, 1252, 41, 283, 908, 705, 447, 807, 1063, 1406, 787, 676, 1557, 14, 714, 1549, 668, 1322, 913, 406, 1107, 40, 362, 724, 505, 18, 670, 517, 924, 716, 444, 497, 306, 609, 1349, 11, 364, 908, 170, 306, 321, 570, 416, 550, 80, 545, 437, 279, 207, 129, 516, 380, 18, 152, 

In [ ]:
np.save("big_igraph_louvain_clusters_node_num.npy", big_igraph_louvain_clusters_node_num)
files.download('big_igraph_louvain_clusters_node_num.npy')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 5.62 ms (started: 2021-02-21 16:30:21 +00:00)


In [ ]:
big_ig_cl_node_num_df = pd.DataFrame(big_igraph_louvain_clusters_node_num)
big_ig_cl_node_num_df.to_csv('big_igraph_louvain_clusters_node_num.csv',index=False)
files.download('big_igraph_louvain_clusters_node_num.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 37.6 ms (started: 2021-02-21 16:30:22 +00:00)


## **3-Infomap**

#### **Igraph - Infomap**

In [ ]:
# Finds the community structure - according to the Infomap method

big_igraph_infomap =  big_igraph.community_infomap(edge_weights=None, vertex_weights=None, trials=10)

time: 18min 23s (started: 2021-02-21 15:21:23 +00:00)


In [ ]:
big_igraph_infomap

time: 5.16 ms (started: 2021-02-21 16:08:03 +00:00)


In [ ]:
print(big_igraph_infomap)

Clustering with 227320 elements and 12451 clusters
[    0] 0, 5, 7, 8, 9, 10, 11, 12, 14, 20, 21, 22, 145712, 145713, 207271,
        207272, 211309, 211318
[    1] 1, 2442, 5689, 23154, 29847, 34155, 55372, 65485, 65486, 65487, 65488,
        81784, 81785, 81786, 95354, 95355, 95356, 96017, 96018, 96019, 98018,
        105036, 132405, 134083, 137235, 148155, 161181, 173682, 173684,
        173685, 173687, 173688, 173689, 173691, 176100, 197585, 197586,
        203925, 203926, 203927, 208854, 208855, 219337, 219338, 223566
[    2] 2, 60420, 72383, 84924, 136264, 136265, 136266, 136267, 136268,
        136269, 136270, 136271, 165090, 165091, 165092, 165093, 198727,
        200217, 222354, 223646
[    3] 3, 97464, 97465, 97466, 97467, 124143, 124144, 124145, 124146, 124147,
        124148, 133992, 167979, 167981, 176928, 176929, 211594, 216081, 227025
[    4] 4, 18, 25344, 83338, 99278, 104187, 111592, 142182, 142183, 142184,
        142186, 142187, 180095, 184989, 196356, 196357, 196358

#### **igraph - InfoMap - Exract cluster properties**

In [ ]:
my_cl_ifm = big_igraph_infomap

time: 972 µs (started: 2021-02-21 16:08:09 +00:00)


In [ ]:
type (big_igraph_infomap)

igraph.clustering.VertexClustering

time: 3.16 ms (started: 2021-02-21 16:08:09 +00:00)


In [ ]:
big_igraph_infomap_cluster_num = len(big_igraph_infomap)
print ('The final number of clusters = ',big_igraph_infomap_cluster_num)

The final number of clusters =  12451
time: 2.6 ms (started: 2021-02-21 16:17:58 +00:00)


In [ ]:
my_infomap_cl_membership_list = my_cl_ifm.membership

time: 2.77 ms (started: 2021-02-21 16:08:12 +00:00)


group nodes by their cluster number  
cluster number was obtaine via my_cl_membership_list varaible  
in the result varaible, we have N sub_list  
each sub_list have Pj member  
j is Sublist ittrator  
and pj is the tottal number of node's that share that cluster  
  
for example sublist # 0, have all node idx which belongs to cluster # 0


In [ ]:
infomap_memb_d = my_infomap_cl_membership_list
ig_comm_infomap_node_group_by_cluster_number = pd.Series(range(len(infomap_memb_d))).groupby(infomap_memb_d, sort=False).apply(list).tolist()

time: 475 ms (started: 2021-02-21 16:08:14 +00:00)


##### **extract each cluster's subgraph and edge list - InfoMap community**

extract subgraph and list of each cluster - here we didnt make super node based graph yet

In [ ]:
cc = 0

for ifm_cluster in my_cl_ifm:

  c_l =len(ifm_cluster)
   
  this_g_name      = 'sb_g_' + str(cc) + '.graphml'
  this_g_edge_name = 'sb_g_' + str(cc) + '_edge.npy'

  np.save(this_g_edge_name, ifm_cluster)

  # files.download(this_g_edge_name)

  cl_g_sb = my_cl_ifm.subgraph(cc)
  
  cl_g_sb.write_graphml(this_g_name)

  # files.download(this_g_name)

  cc=cc+1

time: 3min 28s (started: 2021-02-21 16:08:19 +00:00)


##### **extract each cluster's total cenetrality value - InfoMap**

extract total centrality of each cluster  
cluster centerality = sum of each node's centrality in that cluster  

In [ ]:
# clusters_centerality  = extract_cluster_centerality(centerality_list,cluster_num,node_groupby_cluster):

time: 898 µs (started: 2021-02-21 16:11:48 +00:00)


In [ ]:
infomap_cluster_num = big_igraph_infomap_cluster_num

time: 1.05 ms (started: 2021-02-21 16:18:05 +00:00)


In [ ]:
this_ig_ifmCom_n_gb_cl_num = ig_comm_infomap_node_group_by_cluster_number

time: 891 µs (started: 2021-02-21 16:18:09 +00:00)


###### HIT Centerality

In [ ]:
clusters_infomap_ig_auth_centerality = extract_cluster_centerality(big_igraph_auth_score,infomap_cluster_num,this_ig_ifmCom_n_gb_cl_num)

time: 28.8 ms (started: 2021-02-21 16:18:23 +00:00)


In [ ]:
np.save("clusters_infomap_ig_auth_centerality.npy", clusters_infomap_ig_auth_centerality)
files.download('clusters_infomap_ig_auth_centerality.npy')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 15 ms (started: 2021-02-21 16:18:25 +00:00)


In [ ]:
big_ig_ifm_cl_auth_cen_df = pd.DataFrame(clusters_infomap_ig_auth_centerality)
big_ig_ifm_cl_auth_cen_df.to_csv('clusters_infomap_ig_auth_centerality.csv',index=False)
files.download('clusters_infomap_ig_auth_centerality.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 68 ms (started: 2021-02-21 16:18:25 +00:00)


In [ ]:
clusters_infomap_ig_hub_centerality = extract_cluster_centerality(big_igraph_hub_score,infomap_cluster_num,this_ig_ifmCom_n_gb_cl_num)

time: 34 ms (started: 2021-02-21 16:18:25 +00:00)


In [ ]:
np.save("clusters_infomap_ig_hub_centerality.npy", clusters_infomap_ig_hub_centerality)
files.download('clusters_infomap_ig_hub_centerality.npy')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 7.5 ms (started: 2021-02-21 16:18:25 +00:00)


In [ ]:
big_ig_ifm_cl_hub_cen_df = pd.DataFrame(clusters_infomap_ig_hub_centerality)
big_ig_ifm_cl_hub_cen_df.to_csv('clusters_infomap_ig_hub_centerality.csv',index=False)
files.download('clusters_infomap_ig_hub_centerality.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 74.7 ms (started: 2021-02-21 16:18:25 +00:00)


###### Page Rank Centerality

In [ ]:
clusters_infomap_ig_PRank_centerality = extract_cluster_centerality(big_igraph_PRankH,infomap_cluster_num,this_ig_ifmCom_n_gb_cl_num)

time: 34.8 ms (started: 2021-02-21 16:18:25 +00:00)


In [ ]:
np.save("clusters_infomap_ig_PRank_centerality.npy", clusters_infomap_ig_PRank_centerality)
files.download('clusters_infomap_ig_PRank_centerality.npy')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 7.28 ms (started: 2021-02-21 16:18:25 +00:00)


In [ ]:
big_ig_ifm_cl_PR_cen_df = pd.DataFrame(clusters_infomap_ig_PRank_centerality)
big_ig_ifm_cl_PR_cen_df.to_csv('clusters_infomap_ig_PRank_centerality.csv',index=False)
files.download('clusters_infomap_ig_PRank_centerality.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 74 ms (started: 2021-02-21 16:18:25 +00:00)


###### KShell Centerality

In [ ]:
clusters_infomap_ig_KShell_centerality = extract_cluster_centerality(big_igraph_centerality_KShell,infomap_cluster_num,this_ig_ifmCom_n_gb_cl_num)

time: 24.5 ms (started: 2021-02-21 16:18:29 +00:00)


In [ ]:
np.save("clusters_infomap_ig_KShell_centerality.npy", clusters_infomap_ig_KShell_centerality)
files.download('clusters_infomap_ig_KShell_centerality.npy')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 14.4 ms (started: 2021-02-21 16:18:29 +00:00)


In [ ]:
big_ig_ifm_cl_kshell_cen_df = pd.DataFrame(clusters_infomap_ig_KShell_centerality)
big_ig_ifm_cl_kshell_cen_df.to_csv('clusters_infomap_ig_KShell_centerality.csv',index=False)
files.download('clusters_infomap_ig_KShell_centerality.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 57 ms (started: 2021-02-21 16:18:29 +00:00)


#### igraph - Info MAP === Extract each cluster's totall node number 

In [ ]:
cc = 0

# total_clusters_num = len(my_cl_ifm)

infomap_clusters_node_num = [0] * infomap_cluster_num

for infomap_cluster in my_cl_ifm:

  c_l =len(infomap_cluster)

  # print ('cluster # ', cc , 'size(node num) = ' , c_l)

  infomap_clusters_node_num[cc] = c_l

  cc=cc+1

time: 420 ms (started: 2021-02-21 16:18:30 +00:00)


In [ ]:
len (infomap_clusters_node_num)

12451

time: 3.46 ms (started: 2021-02-21 16:18:30 +00:00)


In [ ]:
# print (clusters_node_num)

time: 1.21 ms (started: 2021-02-21 16:18:30 +00:00)


In [ ]:
big_igraph_infomap_clusters_node_num = infomap_clusters_node_num

time: 1.36 ms (started: 2021-02-21 16:18:30 +00:00)


In [ ]:
print (big_igraph_infomap_clusters_node_num)

[18, 45, 20, 19, 22, 22, 24, 13, 16, 48, 35, 9, 29, 27, 24, 25, 6, 16, 10, 25, 47, 55, 37, 51, 31, 77, 80, 24, 21, 10, 10, 21, 54, 18, 6, 54, 116, 17, 60, 18, 35, 30, 89, 12, 28, 10, 95, 3, 60, 29, 48, 3, 41, 10, 55, 25, 10, 3, 15, 43, 19, 23, 38, 30, 10, 72, 40, 144, 39, 19, 48, 15, 20, 108, 12, 39, 10, 20, 24, 70, 6, 24, 33, 87, 37, 52, 18, 12, 57, 33, 44, 10, 20, 8, 47, 77, 70, 27, 87, 49, 18, 199, 72, 62, 17, 187, 19, 34, 50, 35, 9, 26, 39, 9, 6, 119, 151, 28, 19, 29, 34, 39, 12, 55, 80, 113, 122, 54, 146, 73, 28, 51, 11, 34, 39, 48, 8, 12, 29, 29, 35, 67, 49, 18, 44, 25, 14, 121, 201, 4, 38, 8, 16, 12, 28, 39, 38, 51, 13, 12, 13, 43, 29, 17, 34, 17, 11, 98, 13, 5, 10, 19, 5, 16, 17, 9, 11, 24, 70, 53, 15, 40, 16, 33, 47, 84, 5, 13, 56, 46, 37, 24, 14, 34, 9, 63, 26, 100, 11, 23, 20, 7, 20, 7, 10, 47, 60, 33, 53, 21, 46, 23, 50, 64, 67, 10, 30, 25, 37, 29, 22, 7, 19, 52, 5, 33, 23, 19, 43, 46, 28, 33, 187, 38, 28, 67, 8, 59, 17, 31, 43, 65, 8, 11, 56, 46, 38, 21, 21, 34, 21, 249, 1

In [ ]:
np.save("big_igraph_infomap_clusters_node_num.npy", big_igraph_infomap_clusters_node_num)
files.download('big_igraph_infomap_clusters_node_num.npy')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 9.37 ms (started: 2021-02-21 16:18:31 +00:00)


In [ ]:
big_ig_cl_node_num_ifm_df = pd.DataFrame(big_igraph_infomap_clusters_node_num)
big_ig_cl_node_num_ifm_df.to_csv('big_igraph_infomap_clusters_node_num.csv',index=False)
files.download('big_igraph_infomap_clusters_node_num.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 71.2 ms (started: 2021-02-21 16:18:31 +00:00)


# **New Clustered Graph**


## **1-louvain**

### **extract - louvain clustered graph - SUPER NODE GRAPH**

In [ ]:
big_igraph_clusterd_graph_by_louvain = big_igraph_louvain_best_modularity.cluster_graph(combine_vertices=None, combine_edges=None)

time: 150 ms (started: 2021-02-21 16:30:30 +00:00)


In [ ]:
type (big_igraph_clusterd_graph_by_louvain)

igraph.Graph

time: 2.87 ms (started: 2021-02-21 16:30:30 +00:00)


In [ ]:
ig.summary(big_igraph_clusterd_graph_by_louvain)

IGRAPH U--- 248 7282 -- 
time: 999 µs (started: 2021-02-21 16:30:30 +00:00)


In [ ]:
new_lou = big_igraph_clusterd_graph_by_louvain.copy()

time: 1.38 ms (started: 2021-02-21 16:30:32 +00:00)


In [ ]:
# new_norm_data = norm_func (coef,data,ofset)
def norm_func (coef,data,ofset):
  max_v = max (data)
  min_v = min (data)
  new_norm_data  = [(((x - min_v)/(max_v-min_v))* coef)+ ofset for x in data]
  return new_norm_data

time: 3.88 ms (started: 2021-02-21 16:30:33 +00:00)


In [ ]:
new_louvain_hub_centerality_100 = norm_func (100,clusters_louvain_ig_hub_centerality,0.1)
new_louvain_auth_centerality_100 = norm_func (100,clusters_louvain_ig_auth_centerality,0.1)

time: 1.86 ms (started: 2021-02-21 16:30:35 +00:00)


In [ ]:
len( big_igraph_louvain_clusters_node_num)

248

time: 2.82 ms (started: 2021-02-21 16:30:37 +00:00)


In [ ]:
louvain_vertex_size_normalized

In [ ]:
louvain_vertex_size_normalized = vertex_size_normalized_cal(1000,louvain_cluster_num,big_igraph_louvain_clusters_node_num)

time: 1.04 ms (started: 2021-02-21 16:31:03 +00:00)


In [ ]:
new_lou.vs['PR_centerality'] = clusters_louvain_ig_PRank_centerality
new_lou.vs['hub_centerality'] = clusters_louvain_ig_hub_centerality
new_lou.vs['auth_centerality'] = clusters_louvain_ig_auth_centerality
new_lou.vs['KShell_centerality'] = clusters_louvain_ig_KShell_centerality
new_lou.vs['size_cl'] = louvain_clusters_node_num
new_lou.vs['size_cl_norm_1000'] = louvain_vertex_size_normalized
new_lou.vs['auth_centerality_norm'] = new_louvain_auth_centerality_100
new_lou.vs['hub_centerality_norm']  = new_louvain_hub_centerality_100 

time: 3.88 ms (started: 2021-02-21 16:31:34 +00:00)


In [ ]:
new_lou.write_pajek("new_lou.net")
files.download('new_lou.net')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 6.68 ms (started: 2021-02-21 16:31:38 +00:00)


In [ ]:
new_lou.write_graphml("new_lou2.graphml")
files.download('new_lou2.graphml')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 19.6 ms (started: 2021-02-21 16:31:39 +00:00)


In [ ]:
new_lou.vs.attributes()

['PR_centerality',
 'hub_centerality',
 'auth_centerality',
 'KShell_centerality',
 'size_cl',
 'size_cl_norm_1000',
 'auth_centerality_norm',
 'hub_centerality_norm']

time: 6.98 ms (started: 2021-02-21 16:31:40 +00:00)


### **save - louvain clustered graph**

In [ ]:
big_igraph_clusterd_graph_by_louvain.write_gml('big_igraph_clusterd_graph_by_louvain.gml')
files.download('big_igraph_clusterd_graph_by_louvain.gml')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 12.8 ms (started: 2021-02-21 16:31:47 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_louvain.write_graphml("big_igraph_clusterd_graph_by_louvain.graphml")
files.download('big_igraph_clusterd_graph_by_louvain.graphml')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 10.5 ms (started: 2021-02-21 16:31:47 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_louvain.write_pickle("big_igraph_clusterd_graph_by_louvain.pickle")
files.download('big_igraph_clusterd_graph_by_louvain.pickle')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 13.7 ms (started: 2021-02-21 16:31:47 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_louvain.write_pajek("big_igraph_clusterd_graph_by_louvain.net")
files.download('big_igraph_clusterd_graph_by_louvain.net')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 8.26 ms (started: 2021-02-21 16:31:47 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_louvain.write_pajek("big_igraph_clusterd_graph_by_louvain.pajek")
files.download('big_igraph_clusterd_graph_by_louvain.pajek')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 8.03 ms (started: 2021-02-21 16:31:47 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_louvain.write_edgelist("big_igraph_clusterd_graph_by_louvain.edgelist")
files.download('big_igraph_clusterd_graph_by_louvain.edgelist')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 13.3 ms (started: 2021-02-21 16:31:47 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_louvain.write_dot("big_igraph_clusterd_graph_by_louvain.dot")
files.download('big_igraph_clusterd_graph_by_louvain.dot')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 9.4 ms (started: 2021-02-21 16:31:47 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_louvain.write_dot("big_igraph_clusterd_graph_by_louvain.graphviz")
files.download('big_igraph_clusterd_graph_by_louvain.graphviz')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 9.19 ms (started: 2021-02-21 16:31:47 +00:00)


## **2-Info MAP**

### **extract - Info MAP clustered graph - SUPER NODE GRAPH**

In [ ]:
big_igraph_clusterd_graph_by_infomap = big_igraph_infomap.cluster_graph(combine_vertices=None, combine_edges=None)

time: 176 ms (started: 2021-02-21 16:32:27 +00:00)


In [ ]:
ig.summary(big_igraph_clusterd_graph_by_infomap)

IGRAPH U--- 12451 57574 -- 
time: 2.04 ms (started: 2021-02-21 16:32:28 +00:00)


In [ ]:
new_ifm = big_igraph_clusterd_graph_by_infomap.copy()

time: 2.78 ms (started: 2021-02-21 16:32:29 +00:00)


In [ ]:
infomap_cluster_num

In [ ]:
infomap_vertex_size_normalized = vertex_size_normalized_cal(1000,infomap_cluster_num,big_igraph_infomap_clusters_node_num)

time: 4.38 ms (started: 2021-02-21 16:32:47 +00:00)


In [ ]:
new_infomap_hub_centerality_100 = norm_func (100,clusters_infomap_ig_hub_centerality,0.1)
new_infomap_auth_centerality_100 = norm_func (100,clusters_infomap_ig_auth_centerality,0.1)

time: 8.32 ms (started: 2021-02-21 16:32:48 +00:00)


In [ ]:
new_ifm.vs['PR_centerality'] = clusters_infomap_ig_PRank_centerality
new_ifm.vs['hub_centerality'] = clusters_infomap_ig_hub_centerality
new_ifm.vs['auth_centerality'] = clusters_infomap_ig_auth_centerality
new_ifm.vs['KShell_centerality'] = clusters_infomap_ig_KShell_centerality
new_ifm.vs['size_cl'] = infomap_clusters_node_num
new_ifm.vs['size_cl_norm_1000'] = infomap_vertex_size_normalized
new_ifm.vs['auth_centerality_norm'] = new_infomap_auth_centerality_100
new_ifm.vs['hub_centerality_norm']  = new_infomap_hub_centerality_100 

time: 4.66 ms (started: 2021-02-21 16:32:51 +00:00)


In [ ]:
new_ifm.write_pajek("new_ifm.net")
files.download('new_ifm.net')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 23.8 ms (started: 2021-02-21 16:32:55 +00:00)


In [ ]:
new_ifm.write_graphml("new_ifm2.graphml")
files.download('new_ifm2.graphml')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 142 ms (started: 2021-02-21 16:32:56 +00:00)


In [ ]:
new_ifm.vs.attributes()

['PR_centerality',
 'hub_centerality',
 'auth_centerality',
 'KShell_centerality',
 'size_cl',
 'size_cl_norm_1000',
 'auth_centerality_norm',
 'hub_centerality_norm']

time: 2.89 ms (started: 2021-02-21 16:32:59 +00:00)


### **save - Infomap clustered graph**

In [ ]:
big_igraph_clusterd_graph_by_infomap.write_gml('big_igraph_clusterd_graph_by_infomap.gml')
files.download('big_igraph_clusterd_graph_by_infomap.gml')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 36.8 ms (started: 2021-02-21 16:33:06 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_infomap.write_graphml("big_igraph_clusterd_graph_by_infomap.graphml")
files.download('big_igraph_clusterd_graph_by_infomap.graphml')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 32.8 ms (started: 2021-02-21 16:33:06 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_infomap.write_pickle("big_igraph_clusterd_graph_by_infomap.pickle")
files.download('big_igraph_clusterd_graph_by_infomap.pickle')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 33.6 ms (started: 2021-02-21 16:33:06 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_infomap.write_pajek("big_igraph_clusterd_graph_by_infomap.net")
files.download('big_igraph_clusterd_graph_by_infomap.net')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 23.4 ms (started: 2021-02-21 16:33:06 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_infomap.write_pajek("big_igraph_clusterd_graph_by_infomap.pajek")
files.download('big_igraph_clusterd_graph_by_infomap.pajek')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 23.1 ms (started: 2021-02-21 16:33:06 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_infomap.write_edgelist("big_igraph_clusterd_graph_by_infomap.edgelist")
files.download('big_igraph_clusterd_graph_by_infomap.edgelist')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 26.8 ms (started: 2021-02-21 16:33:06 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_infomap.write_dot("big_igraph_clusterd_graph_by_infomap.dot")
files.download('big_igraph_clusterd_graph_by_infomap.dot')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 27.3 ms (started: 2021-02-21 16:33:06 +00:00)


In [ ]:
big_igraph_clusterd_graph_by_infomap.write_dot("big_igraph_clusterd_graph_by_infomap.graphviz")
files.download('big_igraph_clusterd_graph_by_infomap.graphviz')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

time: 34.6 ms (started: 2021-02-21 16:33:06 +00:00)


## **4-Clauset-Newman - greedy optimization of modularity**

### **Networkx - Clauset-Newman**

In [ ]:
# Find communities in graph using Clauset-Newman-Moore greedy modularity maximization.
big_nx_greedy_modularity_c = list(greedy_modularity_communities(big_nx))

time: 4h 2min 40s (started: 2021-02-21 16:33:34 +00:00)


### **Igraph - Clauset-Newman**

In [ ]:
big_igraph_fastgreedy_Clauset_Newman =  big_igraph.community_fastgreedy(weights=None)

time: 4min 43s (started: 2021-02-21 20:36:14 +00:00)


In [ ]:
print(big_igraph_fastgreedy_Clauset_Newman)

Dendrogram, 227320 elements, 227319 merges
time: 1.82 ms (started: 2021-02-21 20:40:58 +00:00)


In [ ]:
big_igraph_fg =  big_igraph.community_fastgreedy()
print(big_igraph_fg)

Dendrogram, 227320 elements, 227319 merges
time: 4min 44s (started: 2021-02-21 20:40:58 +00:00)


In [ ]:
big_igraph_fg_cl = big_igraph_fg.as_clustering()

time: 97.3 ms (started: 2021-02-21 20:45:42 +00:00)


In [ ]:
for i in range(1,len(big_igraph_fg_cl)+1):
  # print(i)
  print('community #', i , 'is = ' , big_igraph_fg_cl[i-1])
  print('======')

In [ ]:
big_igraph_fg.as_clustering().membership

## **5-Newman on Clustered GRAPH**

### NEWMAN on clusterd_graph_by_louvain

In [ ]:
big_igraph_clusterd_graph_by_louvain_nx = nx.read_graphml("big_igraph_clusterd_graph_by_louvain.graphml")

In [ ]:
big_igraph_clusterd_graph_by_louvain_nx_girvan_newman_communities_generator = community.girvan_newman(big_igraph_clusterd_graph_by_louvain_nx)
